In [88]:
import xml.etree.ElementTree as ET
import numpy as np
import pandas as pd
import re
import os

from pandas import DataFrame

获取 OntologyClass 中的所有 subClass

In [44]:
path = "../data/OntologyClass/"
files = os.listdir(path)
f = open('../data/subClass.txt', 'w')
res = []
for data in files:
    tree = ET.ElementTree(file=path+data)
    name = data.split('.')[0]
    for elem in tree.iter(tag="{http://www.mediawiki.org/xml/export-0.8/}text"):
        text = elem.text
        subClass = re.findall(".*rdfs:subClassOf=(.*)|.*", text)
        for sub in subClass:
            sub = sub.strip('\n')
            if sub != "":
                res.append([name, sub])
                f.write(name+','+sub+'\n')
f.close()

查找没有 subClass 的，然后添加进去

In [49]:
names = []
for i in files:
    names.append(i.split('.')[0])
names1 = np.array(res)[:,0]
ret = list(set(set(names).difference(set(names1))))
f = open('../data/subClass.txt', 'a')
for r in ret:
    f.write(r+',\n')
f.close()

In [50]:
for r in ret:
    print(r)

Skos:OrderedCollection
Identifier
CidocCrm:E4_Period
Medicine
Area
ChartsPlacements
Geo:SpatialThing
GrossDomesticProductPerCapita
Altitude
Diploma
Media
Depth
GrossDomesticProduct
D0:Activity
Gml:_Feature
SportsSeason
Foaf:Image
ChemicalSubstance
Owl:Thing
Statistic
Event
Foaf:Person


查找 OntologyProperty 中的所有 domain

In [ ]:
path = "../data/OntologyProperty/"
files = os.listdir(path)
f = open('../data/domain.txt', 'w')
res = []
for data in files:
    tree = ET.ElementTree(file=path+data)
    name = data.split('.')[0]
    for elem in tree.iter(tag="{http://www.mediawiki.org/xml/export-0.8/}text"):
        text = elem.text
        subClass = re.findall(".*rdfs:domain=(.*)|.*", text)
        for sub in subClass:
            sub = sub.strip('\n')
            if sub != "":
                res.append([name, sub])
                f.write(name+','+sub+'\n')
f.close()

查找没有 domain 的

In [57]:
names = []
for i in files:
    names.append(i.split('.')[0])
names1 = np.array(res)[:,0]
ret = list(set(set(names).difference(set(names1))))
f = open('../data/domain.txt', 'a')
for r in ret:
    f.write(r+',\n')
f.close()

In [56]:
print(len(ret))
# for r in ret:
#     print(r)

390


查找 OntologyProperty 中的所有 range 

In [67]:
path = "../data/OntologyProperty/"
files = os.listdir(path)
f = open('../data/range.txt', 'w')
res = []
for data in files:
    tree = ET.ElementTree(file=path+data)
    name = data.split('.')[0]
    for elem in tree.iter(tag="{http://www.mediawiki.org/xml/export-0.8/}text"):
        text = elem.text
        subClass = re.findall(".*rdfs:range=(.*)|.*", text)
        for sub in subClass:
            sub = sub.strip('\n')
            if sub != "":
                res.append([name, sub])
                f.write(name+','+sub+'\n')
f.close()

In [69]:
names = []
for i in files:
    names.append(i.split('.')[0])
names1 = np.array(res)[:,0]
ret = list(set(set(names).difference(set(names1))))
f = open('../data/range.txt', 'a')
for r in ret:
    f.write(r+',\n')
f.close()
len(ret)

233

尝试生成 class 的树状结构

In [58]:
path = "../data/OntologyClass/"
files = os.listdir(path)
res = []
for data in files:
    tree = ET.ElementTree(file=path+data)
    name = data.split('.')[0]
    for elem in tree.iter(tag="{http://www.mediawiki.org/xml/export-0.8/}text"):
        text = elem.text
        subClass = re.findall(".*rdfs:subClassOf=(.*)|.*", text)
        for sub in subClass:
            sub = sub.strip('\n')
            if sub != "":
                res.append([name, sub])
                

In [59]:
names = []
for i in files:
    names.append(i.split('.')[0])
names1 = np.array(res)[:,0]
roots = list(set(set(names).difference(set(names1))))

In [61]:
class_dict = dict.fromkeys(roots, {})

In [66]:
test = [1, 2, 3, 4]
delete = test.pop(0)
delete

1

将 domain 和 range，补充到 数据集当中

In [76]:
domains = []
f = open('../data/domain.txt', "r")
l = f.readline()
while l:
    l = l.split(',')
    domains.append([l[0], l[1][:-1]])
    l = f.readline()
    
ontologys = np.array(domains)[:,0]
dict_domains = dict.fromkeys(ontologys, "")
for do in domains:
    dict_domains[do[0]] = do[1]

In [95]:
ranges = []
f = open('../data/range.txt', "r")
l = f.readline()
while l:
    l = l.split(',')
    ranges.append([l[0], l[1][:-1]])
    l = f.readline()
    
ontologys = np.array(ranges)[:,0]
dict_ranges = dict.fromkeys(ontologys, "")
for ra in ranges:
    dict_ranges[ra[0]] = ra[1]

In [83]:
datas = pd.read_csv('../data/split.csv')

In [84]:
datas.drop(columns=['Unnamed: 0', '3'], inplace=True)
datas.columns = ['subject', 'property', 'object']

In [86]:
datas.set_index(['property'], inplace=True, drop=False)

In [92]:
datas['domain'] = ""
datas['range'] = ""

In [94]:
datas_list = datas.as_matrix().tolist()

In [112]:
stupid_onto = set()
for d in datas_list:
    title = d[1][0]
    later = d[1][1:]
    title = title.upper()
    d[1] = title + later
    try:
        d[3] = dict_domains[d[1]]
        d[4] = dict_ranges[d[1]]
    except:
        stupid_onto.add(d[1])

In [114]:
for s in stupid_onto:
    print(s)
len(stupid_onto)

Rdf-schema#seeAlso
Homepage
Page
Depiction
Owl#differentFrom
Complete
Subject


7

In [119]:
count = 0
for d in datas_list:
    if d[3] == "":
        count += 1

print("empty domain")
print(count)
print(len(datas_list))

empty domain
6168758
18746175


In [120]:
count = 0
for d in datas_list:
    if d[4] == "":
        count += 1

print("empty range")
print(count)
print(len(datas_list))

empty range
4319640
18746175


In [115]:
res = DataFrame(datas_list, columns=['subject', 'property', 'object', 'domain', 'range'])

In [116]:
for row in res.iterrows():
    print(row)

(0, subject                 Anarchism
property       Rdf-schema#seeAlso
object      Anarchist_terminology
domain                           
range                            
Name: 0, dtype: object)
(1, subject              Anarchism
property    Rdf-schema#seeAlso
object               Anarchism
domain                        
range                         
Name: 1, dtype: object)
(2, subject              Anarchism
property    Rdf-schema#seeAlso
object                  France
domain                        
range                         
Name: 2, dtype: object)
(3, subject              Anarchism
property    Rdf-schema#seeAlso
object                Violence
domain                        
range                         
Name: 3, dtype: object)
(4, subject              Anarchism
property    Rdf-schema#seeAlso
object               Education
domain                        
range                         
Name: 4, dtype: object)
(5, subject           Alabama
property          Country
object      Un

Name: 211, dtype: object)
(212, subject                 Alaska
property    Rdf-schema#seeAlso
object               Dentistry
domain                        
range                         
Name: 212, dtype: object)
(213, subject                 Alaska
property    Rdf-schema#seeAlso
object            Rural_Alaska
domain                        
range                         
Name: 213, dtype: object)
(214, subject                 Alaska
property    Rdf-schema#seeAlso
object         List_of_artists
domain                        
range                         
Name: 214, dtype: object)
(215, subject                  Alaska
property     Rdf-schema#seeAlso
object      Writers_from_Alaska
domain                         
range                          
Name: 215, dtype: object)
(216, subject                 Alaska
property    Rdf-schema#seeAlso
object       List_of_films_set
domain                        
range                         
Name: 216, dtype: object)
(217, subject                     

Name: 370, dtype: object)
(371, subject                                 Alberta
property                     Rdf-schema#seeAlso
object      List_of_Alberta_provincial_highways
domain                                         
range                                          
Name: 371, dtype: object)
(372, subject                Alberta
property    Rdf-schema#seeAlso
object             Health_care
domain                        
range                         
Name: 372, dtype: object)
(373, subject                Alberta
property    Rdf-schema#seeAlso
object                  Canada
domain                        
range                         
Name: 373, dtype: object)
(374, subject                Alberta
property    Rdf-schema#seeAlso
object               Festivals
domain                        
range                         
Name: 374, dtype: object)
(375, subject                Alberta
property    Rdf-schema#seeAlso
object                 Alberta
domain                        
range      

Name: 442, dtype: object)
(443, subject        Albert_Einstein
property    Rdf-schema#seeAlso
object         Einstein_family
domain                        
range                         
Name: 443, dtype: object)
(444, subject             Albert_Einstein
property         Rdf-schema#seeAlso
object      Einstein–Szilárd_letter
domain                             
range                              
Name: 444, dtype: object)
(445, subject              Albert_Einstein
property          Rdf-schema#seeAlso
object      Principle_of_equivalence
domain                              
range                               
Name: 445, dtype: object)
(446, subject                  Allah
property    Rdf-schema#seeAlso
object            Names_of_God
domain                        
range                         
Name: 446, dtype: object)
(447, subject                  Allah
property    Rdf-schema#seeAlso
object              The_Qur'an
domain                        
range                         
Name: 447,

Name: 579, dtype: object)
(580, subject        Attila
property    Successor
object          Ernak
domain               
range                
Name: 580, dtype: object)
(581, subject     Attila
property    Spouse
object       Kreka
domain      Person
range       Person
Name: 581, dtype: object)
(582, subject     Attila
property    Spouse
object      Ildico
domain      Person
range       Person
Name: 582, dtype: object)
(583, subject      Attila
property     Parent
object      Mundzuk
domain       Person
range        Person
Name: 583, dtype: object)
(584, subject     A_Clockwork_Orange_(novel)
property                        Author
object                 Anthony_Burgess
domain                            Work
range                           Person
Name: 584, dtype: object)
(585, subject     A_Clockwork_Orange_(novel)
property                       Country
object                  United_Kingdom
domain                       owl:Thing
range                          Country
Name: 585, dtype: 

...

Name: 25997, dtype: object)
(25998, subject     Global_Climate_Coalition
property                    Homepage
object                           NaN
domain                              
range                               
Name: 25998, dtype: object)
(25999, subject             Home_page
property    Owl#differentFrom
object            Home_screen
domain                       
range                        
Name: 25999, dtype: object)
(26000, subject                Hilter
property    Owl#differentFrom
object           Adolf_Hitler
domain                       
range                        
Name: 26000, dtype: object)
(26001, subject                      Hilter
property          Owl#differentFrom
object      Hitler_(disambiguation)
domain                             
range                              
Name: 26001, dtype: object)
(26002, subject        Hilter
property      Country
object        Germany
domain      owl:Thing
range         Country
Name: 26002, dtype: object)
(26003, subject  

(26157, subject           Holy_See
property            Leader
object      Pietro_Parolin
domain                    
range               Person
Name: 26157, dtype: object)
(26158, subject               Holy_See
property    Rdf-schema#seeAlso
object                Military
domain                        
range                         
Name: 26158, dtype: object)
(26159, subject               Holy_See
property    Rdf-schema#seeAlso
object            Vatican_City
domain                        
range                         
Name: 26159, dtype: object)
(26160, subject                       Honduras
property                        Anthem
object      Himno_Nacional_de_Honduras
domain                                
range                             Work
Name: 26160, dtype: object)
(26161, subject                  Honduras
property           GovernmentType
object      Presidential_republic
domain                           
range              GovernmentType
Name: 26161, dtype: object)
(26162, su

(26303, subject             Heinrich_Hertz
property                 AlmaMater
object        University_of_Berlin
domain                      Person
range       EducationalInstitution
Name: 26303, dtype: object)
(26304, subject     Heinrich_Hertz
property             Field
object             Physics
domain              Artist
range                     
Name: 26304, dtype: object)
(26305, subject             Heinrich_Hertz
property                     Field
object      Electronic_Engineering
domain                      Artist
range                             
Name: 26305, dtype: object)
(26306, subject                Heinrich_Hertz
property                     KnownFor
object      Electromagnetic_radiation
domain                      owl:Thing
range                                
Name: 26306, dtype: object)
(26307, subject           Heinrich_Hertz
property                KnownFor
object      Photoelectric_effect
domain                 owl:Thing
range                           
Name: 26

Name: 26424, dtype: object)
(26425, subject                               Hermann_Göring
property                                       Party
object      National_Socialist_German_Workers'_Party
domain                                     owl:Thing
range                                 PoliticalParty
Name: 26425, dtype: object)
(26426, subject     Hermann_Göring
property             Award
object          Iron_Cross
domain                    
range                Award
Name: 26426, dtype: object)
(26427, subject                       Hermann_Göring
property                               Award
object      Knight's_Cross_of_the_Iron_Cross
domain                                      
range                                  Award
Name: 26427, dtype: object)
(26428, subject                  Hermann_Göring
property                          Award
object      Order_of_the_Zähringer_Lion
domain                                 
range                             Award
Name: 26428, dtype: object)
(26

KeyboardInterrupt: 